In [1]:
# Highest Posterior Density Interval (HPDI) via approximation 
###############################################################################################################
# This generates a highest posterior density interval for draws in vector
# "x".
####################################################################
# KEY in python: x must be a column vector of size (n by 1)!
####################################################################
# The posterior of x, i.e. p(x|y), must be unimodal.
# a is a number between 0 and 1, and indicates the 100(1-a)% desired "level of confidence"
# for the interval. Usually, a will be 0.05. 
# B is the number of bins you want to have for the underlying histogram
# that captures empirical frequencies. The higher this number, the more
# accurate, but slower, is the algorithm. Boost this number until results stabilize.

#note: use of "amin" and "amax" is key to capture min, max of vectors,
#else get array instead of number; alos MUCH faster

def khpdi(x,a,B):
    bw=(amax(x)-amin(x))/B #get bin width
    n = shape(x)[0] #number of rows,that's why we need to send in a column vector
    hist,bin_edges=histogram(x,B,density=False) #get counts for B evenly spaced bins
    h=hist/n #turn into relative frequencies, OK, sums to 1
    
    startmat=array([0]) #initiate vector that will capture lower bounds
    stopmat=array([0]) #initiate vector that will capture upper bounds
    
    for i in range(0,B):
        int=0
        j=i
        while j<B:
            int=int+h[j]
            if int>(1-a):
                startx=amin(x)+i*bw
                stopx=amin(x)+(j+1)*bw
                startmat=append(startmat,startx)
                stopmat=append(stopmat,stopx)
                # (j+1)*bw indicates the lower bound of the jth bin,
                # this is a consevative choice for an upper bound of the HPDI
                break # exit while loop
                #end if condion
            j=j+1
        #end of while loop
    #end of for loop

    # drop leading zeros for startmat, stopmat
    startmat=startmat[1:]
    stopmat=stopmat[1:]

    # now we need to find the smallest of these intervals
    #####################################################
    # first, convert everything to vectors so we can sort
    # over rows below
    rs=len(startmat) #get number of elements in startmat

    startmat.shape=(rs,1) #convert to vector
    stopmat.shape=(rs,1) #convert to vector
    rangemat=stopmat-startmat

    #combine all 3 columns
    allmat=concatenate((rangemat,startmat,stopmat),axis=1)
    # sort by first column - smallest to largest range
    all=allmat[argsort(allmat[:,0])]

    L=all[0,1]
    U=all[0,2]
   
    return(L,U)